In [8]:
import numpy as np
import geopandas as gpd
import fiona
import pandas as pd
import rasterio
from rasterio.mask import mask
from shapely.geometry import MultiPolygon
from rasterstats import zonal_stats
import folium

data_dir = '../data'

# Load the raster
slope_raster = rasterio.open(data_dir + '/derived_data/slope_zurich.tif')

# Load the data and ensure CRS matches the raster
tree_dataset = gpd.read_file(data_dir + '/raw_data/geodata_stadt_Zuerich/trees/data/data.gpkg').to_crs(slope_raster.crs)
flats_duration = gpd.read_file(data_dir + '/derived_data/flats_duration.gpkg').to_crs(slope_raster.crs)
parking_lots = gpd.read_file(data_dir + '/raw_data/osm_data/parking_lots_zurich.gpkg').to_crs(slope_raster.crs)
rcps = gpd.read_file(data_dir + '/raw_data/geodata_stadt_Zuerich/recycling_sammelstellen/data/stzh.poi_sammelstelle_view.shp').to_crs(slope_raster.crs)

# List all layers in the vbz geopackage
layers = fiona.listlayers(data_dir + '/raw_data/geodata_stadt_Zuerich/vbz/data/data.gpkg')
line_layers = []
point_layers = []

# Loop through layers and separate those that contain only line or point geometries
for layer in layers:
    gdf = gpd.read_file(data_dir + '/raw_data/geodata_stadt_Zuerich/vbz/data/data.gpkg', layer=layer)
    if gdf.geom_type.str.startswith("Line").all():
        line_layers.append(gdf)
    elif gdf.geom_type.str.startswith("Point").all():
        point_layers.append(gdf)

# Merge all line layers into one GeoDataFrame
vbz_lines = gpd.GeoDataFrame(
    pd.concat(line_layers, ignore_index=True), crs=line_layers[0].crs
)

# Merge all point layers into one GeoDataFrame
vbz_points = gpd.GeoDataFrame(
    pd.concat(point_layers, ignore_index=True), crs=point_layers[0].crs
)

# Reproject all data to the same CRS as the raster
vbz_lines = vbz_lines.to_crs(slope_raster.crs)
vbz_points = vbz_points.to_crs(slope_raster.crs)
tree_dataset = tree_dataset.to_crs(slope_raster.crs)
parking_lots = parking_lots.to_crs(slope_raster.crs)


/home/silas/miniconda3/envs/geoenv/lib/python3.10/site-packages/geopandas/io/file.py:399: FutureWarning: errors='ignore' is deprecated and will raise in a future version. Use to_datetime without passing `errors` and catch exceptions explicitly instead
  as_dt = pd.to_datetime(df[k], errors="ignore")


In [4]:

def suitability_analysis(
    buffer_dist_vbz: float,
    area_threshold: float,
    buffer_trees: float,
    max_slope: float,
    parking_lots: gpd.GeoDataFrame,
    slope_raster: rasterio.DatasetReader,
    trees: gpd.GeoDataFrame,
    vbz_lines: gpd.GeoDataFrame,
    vbz_points: gpd.GeoDataFrame
):
    # Step 1: Filter parking types
    parking_filtered = parking_lots[
        ~parking_lots['parking'].isin(['underground', 'multi-storey'])
    ].copy()

    # Step 2: Process VBZ features
    vbz_line_buffers = vbz_lines.buffer(buffer_dist_vbz)
    vbz_point_buffers = vbz_points.buffer(buffer_dist_vbz)

    # Step 3: Buffer trees
    tree_buffers = trees.buffer(buffer_trees)

    # Step 4: Combine all buffers
    all_buffers = gpd.GeoSeries(
        list(vbz_line_buffers) + list(vbz_point_buffers) + list(tree_buffers),
        crs=parking_lots.crs
    ).unary_union

    # Step 5: Zonal statistics for slope
    slope_stats = zonal_stats(
        parking_filtered,
        slope_raster.name,  # Use the raster filepath from the raster object
        stats=['mean', 'max'],
        nodata=slope_raster.nodata
    )

    # Add slope stats to parking lots
    parking_filtered['slope_mean'] = [s['mean'] for s in slope_stats]
    parking_filtered['slope_max'] = [s['max'] for s in slope_stats]

    # Step 6: Filter by slope
    slope_filtered = parking_filtered[parking_filtered['slope_mean'] <= max_slope]

    # Step 7: Spatial difference with buffers
    final_areas = slope_filtered.geometry.difference(all_buffers)

    # Step 8: Calculate areas and filter
    result = gpd.GeoDataFrame(geometry=final_areas, crs=parking_lots.crs)
    result['area'] = result.geometry.area
    suitable = result[result['area'] >= area_threshold]

    return suitable


In [ ]:
# Define parameters
buffer_dist_vbz = 2  # 50 meters buffer around VBZ infrastructure
buffer_trees = 2     # 10 meters buffer around trees
max_slope = 5       # Maximum slope of 15 degrees
area_threshold = 16  # Minimum area of 1000 square meters

# Apply suitability analysis
suitable_areas = suitability_analysis(
    area_threshold=area_threshold,
    buffer_dist_vbz=buffer_dist_vbz,
    buffer_trees=buffer_trees,
    max_slope=max_slope,
    parking_lots=parking_lots,
    slope_raster=slope_raster,
    trees=tree_dataset,
    vbz_lines=vbz_lines,
    vbz_points=vbz_points
)

In [ ]:
# export the result to a GeoPackage
suitable_areas.to_file(data_dir + '/derived_data/potential_locations.gpkg', driver='GPKG')

# Assign unique IDs to existing sites and add status
existing_sites = rcps.copy()
existing_sites['ID'] = ['e_{}'.format(i+1) for i in existing_sites.index]
existing_sites['status'] = 'open'
existing_sites = existing_sites[['geometry', 'ID', 'status']]

# Create a buffer of 99 meters around existing open sites
buffer = existing_sites.geometry.buffer(125)

# Merge all buffers into a single geometry
buffer_union = buffer.unary_union

# Filter out potential sites within the buffer BEFORE merging
filtered_potential_sites = suitable_areas[~suitable_areas.geometry.intersects(buffer_union)].copy()

# Add unique IDs and status to filtered potential sites
filtered_potential_sites['ID'] = ['p_{}'.format(i+1) for i in filtered_potential_sites.index]
filtered_potential_sites['status'] = 'potential'
filtered_potential_sites = filtered_potential_sites[['geometry', 'ID', 'status']]

# Merge the existing and filtered potential sites; merged df preserves the status column
merged_sites = pd.concat([existing_sites, filtered_potential_sites], ignore_index=True)

# Export the merged sites to a GeoPackage
merged_sites.to_file(data_dir + '/derived_data/all_sites.gpkg', driver='GPKG')

In [9]:
# Create a base map centered on Zurich
m = folium.Map(location=[47.3769, 8.5417], zoom_start=12)

# Add suitable areas to the map
folium.GeoJson(
    suitable_areas,
    name='Suitable Areas',
    tooltip=folium.GeoJsonTooltip(fields=['area'], aliases=['Area'])
).add_to(m)

# Display the map
m

In [27]:
from sklearn.cluster import KMeans

# Compute centroids coordinates from suitable_areas
suitable_areas['centroid'] = suitable_areas.geometry.centroid
coords = np.array([[pt.x, pt.y] for pt in suitable_areas['centroid']])

# Set number of clusters
n_clusters = 450

# Run KMeans clustering
kmeans = KMeans(n_clusters=n_clusters, random_state=0).fit(coords)
cluster_centers = kmeans.cluster_centers_

# For each cluster center, find the suitable_area centroid closest to it
selected_indices = []
for center in cluster_centers:
    distances = np.linalg.norm(coords - center, axis=1)
    closest_index = np.argmin(distances)
    selected_indices.append(closest_index)

# Remove any duplicate selections if they occur
selected_indices = list(set(selected_indices))

# Create a GeoDataFrame with the representative sites
selected_sites = suitable_areas.iloc[selected_indices].copy()

selected_sites

geometry         area  \
6     POLYGON ((2680974.204 1245218.009, 2680986.437...  9406.352080   
9     POLYGON ((2682869.693 1246153.332, 2682888.527...  3657.715865   
10    POLYGON ((2682104.887 1243275.285, 2682108.346...   292.187718   
11    POLYGON ((2684909.069 1244836.861, 2684897.379...  2221.041761   
12    POLYGON ((2678248.034 1248514.835, 2678253.350...  3242.406862   
...                                                 ...          ...   
9059  POLYGON ((2684246.847 1245635.495, 2684247.901...    55.472492   
9152  POLYGON ((2681928.575 1245555.854, 2681928.703...    84.975983   
9170  POLYGON ((2680456.024 1253281.663, 2680479.762...   780.399694   
9171  POLYGON ((2680407.194 1253163.256, 2680402.417...   589.157775   
9197  POLYGON ((2679993.885 1247848.954, 2680042.749...   884.594968   

                             centroid  
6     POINT (2680927.794 1245158.751)  
9     POINT (2682882.027 1246072.947)  
10    POINT (2682095.407 1243244.755)  
11    POINT (2684880.898 1244870.498)  
12    POINT (2678277.621 1248471.687)  
...                               ...  
9059  POINT (2684255.744 1245621.475)  
9152  POINT (2681933.784 1245548.138)  
9170  POINT (2680484.430 1253282.812)  
9171  POINT (2680410.668 1253176.536)  
9197  POINT (2680012.535 1247828.152)  

[450 rows x 3 columns]

In [28]:
# Create a base map centered on Zurich
m = folium.Map(location=[47.3769, 8.5417], zoom_start=12)

selected_sites.drop(columns='centroid', inplace=True)   
# Add selected sites to the map
folium.GeoJson(
    selected_sites,
    name='Selected Sites',
    tooltip=folium.GeoJsonTooltip(fields=['area'], aliases=['Area'])
).add_to(m)

# Display the map
m